(TutorialLearner1D)=
# Tutorial {class}`~adaptive.Learner1D`

```{note}
Because this documentation consists of static html, the `live_plot` and `live_info` widget is not live.
Download the notebook in order to see the real behaviour. [^download]
```

In [1]:
import adaptive

adaptive.notebook_extension()

import numpy as np
from functools import partial
import random

## scalar output: `f:ℝ → ℝ`

We start with the most common use-case: sampling a 1D function `f: ℝ → ℝ`.

We will use the following function, which is a smooth (linear) background with a sharp peak at a random location:

In [2]:
offset = random.uniform(-0.5, 0.5)


def f(x, offset=offset, wait=True):
    from time import sleep
    from random import random

    a = 0.01
    if wait:
        sleep(random() / 10)
    return x + a**2 / (a**2 + (x - offset) ** 2)

We start by initializing a 1D “learner”, which will suggest points to evaluate, and adapt its suggestions as more and more points are evaluated.

In [3]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))

Next we create a “runner” that will request points from the learner and evaluate ‘f’ on them.

By default on Unix-like systems the runner will evaluate the points in parallel using local processes {class}`concurrent.futures.ProcessPoolExecutor`.

On Windows systems the runner will use a {class}`loky.get_reusable_executor`.
A {class}`~concurrent.futures.ProcessPoolExecutor` cannot be used on Windows for reasons.

In [4]:
# The end condition is when the "loss" is less than 0.1. In the context of the
# 1D learner this means that we will resolve features in 'func' with width 0.1 or wider.
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [5]:
await runner.task  # This is not needed in a notebook environment!

When instantiated in a Jupyter notebook the runner does its job in the background and does not block the IPython kernel.
We can use this to create a plot that updates as new data arrives:

In [6]:
runner.live_info()

In [7]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

We can now compare the adaptive sampling to a homogeneous sampling with the same number of points:

In [8]:
if not runner.task.done():
    raise RuntimeError(
        "Wait for the runner to finish before executing the cells below!"
    )

In [9]:
learner2 = adaptive.Learner1D(f, bounds=learner.bounds)

xs = np.linspace(*learner.bounds, len(learner.data))
learner2.tell_many(xs, map(partial(f, wait=False), xs))

learner.plot() + learner2.plot()

:Layout
   .Overlay.I  :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.II :Overlay
      .Scatter.I :Scatter   [x]   (y)

## vector output: `f:ℝ → ℝ^N`

Sometimes you may want to learn a function with vector output:

In [10]:
random.seed(0)
offsets = [random.uniform(-0.8, 0.8) for _ in range(3)]

# sharp peaks at random locations in the domain
def f_levels(x, offsets=offsets):
    a = 0.01
    return np.array(
        [offset + x + a**2 / (a**2 + (x - offset) ** 2) for offset in offsets]
    )

`adaptive` has you covered!
The `Learner1D` can be used for such functions:

In [11]:
learner = adaptive.Learner1D(f_levels, bounds=(-1, 1))
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [12]:
await runner.task  # This is not needed in a notebook environment!

/home/docs/checkouts/readthedocs.org/user_builds/adaptive/conda/v0.14.0/lib/python3.9/site-packages/numpy/lib/nanfunctions.py:96: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  a = np.asanyarray(a)


In [13]:
runner.live_info()

In [14]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I   :Scatter   [x]   (y)
      .Scatter.II  :Scatter   [x]   (y)
      .Scatter.III :Scatter   [x]   (y)

## Looking at curvature

By default `adaptive` will sample more points where the (normalized) euclidean distance between the neighboring points is large.
You may achieve better results sampling more points in regions with high curvature.
To do this, you need to tell the learner to look at the curvature by specifying `loss_per_interval`.

In [15]:
from adaptive.learner.learner1D import (
    curvature_loss_function,
    uniform_loss,
    default_loss,
)

curvature_loss = curvature_loss_function()
learner = adaptive.Learner1D(f, bounds=(-1, 1), loss_per_interval=curvature_loss)
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [16]:
await runner.task  # This is not needed in a notebook environment!

In [17]:
runner.live_info()

In [18]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

We may see the difference of homogeneous sampling vs only one interval vs including the nearest neighboring intervals in this plot.
We will look at 100 points.

In [19]:
def sin_exp(x):
    from math import exp, sin

    return sin(15 * x) * exp(-(x**2) * 2)


learner_h = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=uniform_loss)
learner_1 = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=default_loss)
learner_2 = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=curvature_loss)

npoints_goal = lambda l: l.npoints >= 100
# adaptive.runner.simple is a non parallel blocking runner.
adaptive.runner.simple(learner_h, goal=npoints_goal)
adaptive.runner.simple(learner_1, goal=npoints_goal)
adaptive.runner.simple(learner_2, goal=npoints_goal)

(
    learner_h.plot().relabel("homogeneous")
    + learner_1.plot().relabel("euclidean loss")
    + learner_2.plot().relabel("curvature loss")
).cols(2)

:Layout
   .Overlay.Homogeneous    :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Euclidean_loss :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Curvature_loss :Overlay
      .Scatter.I :Scatter   [x]   (y)

More info about using custom loss functions can be found in {ref}`Custom adaptive logic for 1D and 2D`.

## Exporting the data

We can view the raw data by looking at the dictionary `learner.data`.
Alternatively, we can view the data as NumPy array with

In [20]:
learner.to_numpy()

array([[-1.        , -0.99993838],
       [-0.75      , -0.74990462],
       [-0.5       , -0.49983304],
       [-0.25      , -0.24963574],
       [-0.125     , -0.12437181],
       [ 0.        ,  0.00133158],
       [ 0.0625    ,  0.06473351],
       [ 0.125     ,  0.12949258],
       [ 0.15625   ,  0.16342782],
       [ 0.1875    ,  0.20073133],
       [ 0.21875   ,  0.25062795],
       [ 0.2265625 ,  0.26935374],
       [ 0.234375  ,  0.29465374],
       [ 0.25      ,  0.39942416],
       [ 0.25390625,  0.45466963],
       [ 0.2578125 ,  0.53754893],
       [ 0.26171875,  0.66595923],
       [ 0.265625  ,  0.86159666],
       [ 0.26953125,  1.11180314],
       [ 0.27148438,  1.21812019],
       [ 0.2734375 ,  1.27166685],
       [ 0.27734375,  1.16903987],
       [ 0.28125   ,  0.92794728],
       [ 0.28515625,  0.72445512],
       [ 0.2890625 ,  0.5910344 ],
       [ 0.29296875,  0.50793218],
       [ 0.296875  ,  0.45566773],
       [ 0.3046875 ,  0.39988777],
       [ 0.3125    ,

If Pandas is installed (optional dependency), you can also run

In [21]:
df = learner.to_dataframe()
df

x         y function.offset function.wait
0  -1.000000 -0.999938        0.273859          True
1  -0.750000 -0.749905        0.273859          True
2  -0.500000 -0.499833        0.273859          True
3  -0.250000 -0.249636        0.273859          True
4  -0.125000 -0.124372        0.273859          True
5   0.000000  0.001332        0.273859          True
6   0.062500  0.064734        0.273859          True
7   0.125000  0.129493        0.273859          True
8   0.156250  0.163428        0.273859          True
9   0.187500  0.200731        0.273859          True
10  0.218750  0.250628        0.273859          True
11  0.226562  0.269354        0.273859          True
12  0.234375  0.294654        0.273859          True
13  0.250000  0.399424        0.273859          True
14  0.253906  0.454670        0.273859          True
15  0.257812  0.537549        0.273859          True
16  0.261719  0.665959        0.273859          True
17  0.265625  0.861597        0.273859          True
18  0.269531  1.111803        0.273859          True
19  0.271484  1.218120        0.273859          True
20  0.273438  1.271667        0.273859          True
21  0.277344  1.169040        0.273859          True
22  0.281250  0.927947        0.273859          True
23  0.285156  0.724455        0.273859          True
24  0.289062  0.591034        0.273859          True
25  0.292969  0.507932        0.273859          True
26  0.296875  0.455668        0.273859          True
27  0.304688  0.399888        0.273859          True
28  0.312500  0.375269        0.273859          True
29  0.328125  0.360967        0.273859          True
30  0.343750  0.363811        0.273859          True
31  0.375000  0.384681        0.273859          True
32  0.437500  0.441220        0.273859          True
33  0.500000  0.501952        0.273859          True
34  0.625000  0.625810        0.273859          True
35  0.750000  0.750441        0.273859          True
36  0.875000  0.875277        0.273859          True
37  1.000000  1.000190        0.273859          True

and load that data into a new learner with

In [22]:
new_learner = adaptive.Learner1D(learner.function, (-1, 1))  # create an empty learner
new_learner.load_dataframe(df)  # load the pandas.DataFrame's data
new_learner.plot()

:Overlay
   .Scatter.I :Scatter   [x]   (y)

[^download]: This notebook can be downloaded as **{nb-download}`tutorial.Learner1D.ipynb`** and {download}`tutorial.Learner1D.md`.